If you're opening this Notebook on colab, you will probably need to install 🤗 Transformers and 🤗 Datasets. Uncomment the following cell and run it.

In [ ]:
! pip install datasets transformers

In [ ]:
import transformers

print(transformers.__version__)

4.35.2


# Fine-tuning a model on a question-answering task

In [ ]:
squad_v2 = False
model_checkpoint = "distilbert-base-uncased"
batch_size = 16

## Loading the dataset

In [ ]:
from datasets import load_dataset, load_metric


In [ ]:
datasets = load_dataset("json", data_files='alldata.json',field='data')

The `datasets` object itself is [`DatasetDict`](https://huggingface.co/docs/datasets/package_reference/main_classes.html#datasetdict), which contains one key for the training set.

We can see the training have a column for the context, the question and the answers to those questions.

To access an actual element, you need to select a split first, then give an index:

In [ ]:
datasets["train"][0]

{'id': 'eb74840dbbd0840cffe3f1ad4ad5da1f',
 'answers': [{'input_text': 'যুক্তরাষ্ট্রের',
   'span_end': 84,
   'span_start': 0,
   'span_text': 'টিকফা চুক্তিতে স্বাক্ষর করলে বাংলাদেশের জাতীয় নিরাপত্তা যুক্তরাষ্ট্রের হাতে চলে যাবে',
   'turn_id': 1},
  {'input_text': 'বাংলাদেশের ওয়ার্কার্স পার্টির পলিটব্যুরোর সভায় গৃহীত প্রস্তাবে',
   'span_end': 177,
   'span_start': 0,
   'span_text': 'টিকফা চুক্তিতে স্বাক্ষর করলে বাংলাদেশের জাতীয় নিরাপত্তা যুক্তরাষ্ট্রের হাতে চলে যাবে। গতকাল সোমবার বাংলাদেশের ওয়ার্কার্স পার্টির পলিটব্যুরোর সভায় গৃহীত প্রস্তাবে এ কথা বলা হয়',
   'turn_id': 2},
  {'input_text': '১৯ মে রোববার',
   'span_end': 261,
   'span_start': 199,
   'span_text': '১৯ মে রোববার দেশব্যাপী বিক্ষোভ দিবস পালন করার আহ্বান জানানো হয়',
   'turn_id': 3},
  {'input_text': 'রাশেদ খান ',
   'span_end': 284,
   'span_start': 263,
   'span_text': 'দলের সভাপতি রাশেদ খান ',
   'turn_id': 4}],
 'question': [{'input_text': 'টিকফা চুক্তিতে স্বাক্ষর করলে বাংলাদেশের জাতীয় নিরাপত্তা কাদের হাতে 

We can see the answers are indicated by their start position in the text (here at character 515) and their full text, which is a substring of the context as we mentioned above.

To get a sense of what the data looks like, the following function will show some examples picked randomly in the dataset (automatically decoding the labels in passing).

In [ ]:
from datasets import ClassLabel, Sequence
import random
import pandas as pd
from IPython.display import display, HTML

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)

    df = pd.DataFrame(dataset[picks])
    for column, typ in dataset.features.items():
        if isinstance(typ, ClassLabel):
            df[column] = df[column].transform(lambda i: typ.names[i])
        elif isinstance(typ, Sequence) and isinstance(typ.feature, ClassLabel):
            df[column] = df[column].transform(lambda x: [typ.feature.names[i] for i in x])
    display(HTML(df.to_html()))

In [ ]:
show_random_elements(datasets["train"])

## Preprocessing the training data

Before we can feed those texts to our model, we need to preprocess them. This is done by a 🤗 Transformers `Tokenizer` which will (as the name indicates) tokenize the inputs (including converting the tokens to their corresponding IDs in the pretrained vocabulary) and put it in a format the model expects, as well as generate the other inputs that model requires.

To do all of this, we instantiate our tokenizer with the `AutoTokenizer.from_pretrained` method, which will ensure:

- we get a tokenizer that corresponds to the model architecture we want to use,
- we download the vocabulary used when pretraining this specific checkpoint.

That vocabulary will be cached, so it's not downloaded again the next time we run the cell.

In [ ]:
import json
from transformers import AutoModelForQuestionAnswering, AutoTokenizer
import torch
import random

# Load the pre-trained model and tokenizer
model_path = "shams/banglabert-finetuned-squad"
tokenizer_path = "distilbert-base-uncased"
model = AutoModelForQuestionAnswering.from_pretrained(model_path)
tokenizer = AutoTokenizer.from_pretrained(tokenizer_path)

The following assertion ensures that our tokenizer is a fast tokenizers (backed by Rust) from the 🤗 Tokenizers library. Those fast tokenizers are available for almost all models, and we will need some of the special features they have for our preprocessing.

In [ ]:
import transformers
assert isinstance(tokenizer, transformers.PreTrainedTokenizerFast)

You can check which type of models have a fast tokenizer available and which don't on the [big table of models](https://huggingface.co/transformers/index.html#bigtable).

You can directly call this tokenizer on two sentences (one for the answer, one for the context):

In [ ]:
tokenizer("আপনার নাম কি?", "আমার নাম নিকুঞ্জো.")

{'input_ids': [101, 1348, 29903, 29902, 29914, 29908, 1366, 29914, 29906, 1353, 29915, 1029, 102, 1348, 29906, 29914, 29908, 1366, 29914, 29906, 100, 1012, 102], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]}

Depending on the model you selected, you will see different keys in the dictionary returned by the cell above. They don't matter much for what we're doing here (just know they are required by the model we will instantiate later), you can learn more about them in [this tutorial](https://huggingface.co/transformers/preprocessing.html) if you're interested.

Now one specific thing for the preprocessing in question answering is how to deal with very long documents. We usually truncate them in other tasks, when they are longer than the model maximum sentence length, but here, removing part of the the context might result in losing the answer we are looking for. To deal with this, we will allow one (long) example in our dataset to give several input features, each of length shorter than the maximum length of the model (or the one we set as a hyper-parameter). Also, just in case the answer lies at the point we split a long context, we allow some overlap between the features we generate controlled by the hyper-parameter `doc_stride`:

In [ ]:
max_length = 384 # The maximum length of a feature (question and context)
doc_stride = 128 # The authorized overlap between two part of the context when splitting it is needed.

Let's find one long example in our dataset:

In [ ]:
for i, example in enumerate(datasets["train"]):
    ##print(example['story'])
    tokenized_input= tokenizer(example['story'])
    input_ids=tokenized_input["input_ids"]
    print(input_ids)


Token indices sequence length is longer than the specified maximum sequence length for this model (2498 > 512). Running this sequence through the model will result in indexing errors


[101, 100, 1356, 29889, 29898, 29915, 29898, 29917, 1376, 29904, 29914, 29889, 29911, 29908, 1353, 29908, 29909, 29917, 1368, 29914, 29882, 29909, 29914, 29900, 29917, 29910, 29917, 29908, 1358, 29914, 29898, 29916, 29907, 1366, 29915, 29908, 29914, 29903, 29898, 29898, 29914, 1371, 29889, 29898, 29908, 29914, 29911, 29895, 29908, 29917, 29908, 1377, 29914, 29898, 29917, 1356, 29909, 29917, 1371, 29914, 29904, 29917, 1344, 1355, 29898, 29889, 29914, 29909, 1376, 29917, 29914, 29906, 29904, 29914, 29908, 1368, 29914, 29882, 29909, 29914, 29900, 29917, 29910, 29917, 29908, 1352, 29907, 29914, 29908, 29889, 29914, 29908, 29912, 1367, 29914, 29908, 29895, 29915, 29908, 1367, 29909, 29915, 29895, 29904, 29907, 29908, 29917, 29914, 29908, 1376, 29905, 29914, 29907, 1355, 29913, 29916, 29898, 1367, 29908, 29912, 29898, 29914, 29904, 29917, 1351, 1353, 29899, 29914, 1368, 29909, 29914, 1377, 29907, 1344, 1351, 1356, 29889, 29898, 29915, 29908, 1367, 29908, 29898, 29915, 29904, 29914, 29900, 29

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[101, 1351, 29889, 29917, 29908, 1367, 29908, 1351, 29889, 1377, 29908, 29898, 29914, 29909, 1352, 100, 1347, 29912, 29899, 29915, 29908, 29898, 29914, 29907, 1364, 29917, 29910, 29917, 29908, 1374, 29915, 29889, 29911, 29914, 29904, 29907, 29904, 29912, 29899, 29914, 29907, 1376, 29899, 29904, 29915, 29908, 29898, 29914, 1366, 29917, 29906, 29917, 1351, 29912, 29917, 29893, 29917, 1344, 1376, 29914, 29908, 29914, 1368, 29893, 29908, 29917, 29908, 1358, 29902, 29907, 1353, 29908, 29914, 100, 1351, 29889, 29914, 29896, 29917, 29906, 29915, 29889, 1353, 29907, 29914, 29909, 29917, 29902, 29896, 29914, 29908, 1367, 29914, 29892, 1370, 29914, 29912, 29917, 29885, 1352, 29909, 29895, 29903, 29914, 29909, 29895, 1377, 29907, 29917, 1355, 29917, 29893, 29917, 1344, 1353, 29909, 29914, 29912, 29903, 29908, 29916, 29889, 29911, 29914, 1367, 29915, 29893, 29915, 29907, 29917, 1355, 29915, 29907, 29917, 1356, 29908, 29906, 1376, 29882, 29889, 29895, 29917, 29908, 1370, 29890, 29917, 1367, 29896,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
for i, example in enumerate(datasets["train"]):

    tokenized_input= tokenizer(example['question'][0]["input_text"])
    input_ids=tokenized_input["input_ids"]
    print(input_ids)


In [ ]:
for i, example in enumerate(datasets["train"]):
    if len(tokenizer(example['question'][0]["input_text"], example['story'])["input_ids"]) > 384:
        break
example = datasets["train"][i]


Without any truncation, we get the following length for the input IDs:

In [ ]:
len(tokenizer(example['question'][0]["input_text"], example["story"])["input_ids"])

301

Now, if we just truncate, we will lose information (and possibly the answer to our question):

In [ ]:
len(tokenizer(example['question'][0]["input_text"], example["story"], max_length=max_length, truncation="only_second")["input_ids"])

301

Note that we never want to truncate the question, only the context, else the `only_second` truncation picked. Now, our tokenizer can automatically return us a list of features capped by a certain maximum length, with the overlap we talked above, we just have to tell it with `return_overflowing_tokens=True` and by passing the stride:

In [ ]:
tokenized_example = tokenizer(
    example['question'][0]["input_text"],
    example["story"],
    max_length=max_length,
    truncation="only_second",
    return_overflowing_tokens=True,
    stride=doc_stride
)

Now we don't have one list of `input_ids`, but several:

In [ ]:
[len(x) for x in tokenized_example["input_ids"]]

[301]

And if we decode them, we can see the overlap:

In [ ]:
for x in tokenized_example["input_ids"][:2]:
    print(tokenizer.decode(x))

[CLS] কবে থেকে নিযমিতই পেযাজ আসবে? [SEP] [UNK] ধারণা করা হচছে ডিসেমবর থেকে নিযমিতই পেযাজ আসবে চটটগরাম দিযে । চটটগরাম বনদর দিযে পরথমবার বড পেযাজের চালান আমদানির পর বধবার ও বহসপতিবার সারাদিনই আলোচনার বিষয ছিল বিএসএম গরপের পেযাজ । আজ [UNK] [UNK] পর বাজারে কিছটা ইতিবাচক পরভাব পডেছে । আজ চীনের পেযাজের দাম কেজি [UNK] টাকা কমে [UNK] থেকে [UNK] টাকায বিকরি হযেছে । মিযানমারের পেযাজের দামও কেজি [UNK] টাকা কমেছে । [SEP]


Now this will give us some work to properly treat the answers: we need to find in which of those features the answer actually is, and where exactly in that feature. The models we will use require the start and end positions of these answers in the tokens, so we will also need to to map parts of the original context to some tokens. Thankfully, the tokenizer we're using can help us with that by returning an `offset_mapping`:

In [ ]:
tokenized_example = tokenizer(
    example['question'][0]["input_text"],
    example["story"],
    max_length=max_length,
    truncation="only_second",
    return_overflowing_tokens=True,
    return_offsets_mapping=True,
    stride=doc_stride
)
print(tokenized_example["offset_mapping"][0][:100])

[(0, 0), (0, 1), (1, 2), (2, 3), (4, 5), (5, 6), (6, 7), (7, 8), (9, 10), (10, 11), (11, 12), (12, 13), (13, 14), (14, 15), (15, 16), (17, 18), (18, 19), (20, 21), (21, 22), (22, 23), (24, 25), (25, 26), (26, 27), (27, 28), (28, 29), (0, 0), (0, 8), (9, 10), (10, 11), (11, 12), (12, 13), (13, 14), (15, 16), (16, 17), (17, 18), (19, 20), (20, 21), (22, 23), (23, 24), (25, 26), (26, 27), (27, 28), (28, 29), (29, 30), (31, 32), (32, 33), (34, 35), (35, 36), (36, 37), (37, 38), (39, 40), (40, 41), (41, 42), (42, 43), (43, 44), (44, 45), (45, 46), (47, 48), (48, 49), (50, 51), (51, 52), (52, 53), (54, 55), (55, 56), (56, 57), (57, 58), (59, 60), (60, 61), (62, 63), (63, 64), (65, 66), (66, 67), (67, 68), (69, 70), (70, 71), (71, 72), (72, 73), (73, 74), (75, 76), (76, 77), (78, 79), (79, 80), (81, 82), (82, 83), (83, 84), (85, 86), (86, 87), (88, 89), (89, 90), (91, 92), (92, 93), (93, 94), (94, 95), (96, 97), (98, 99), (99, 100), (100, 101), (101, 102), (102, 103), (103, 104)]


This gives, for each index of our input IDS, the corresponding start and end character in the original text that gave our token. The very first token (`[CLS]`) has (0, 0) because it doesn't correspond to any part of the question/answer, then the second token is the same as the characters 0 to 3 of the question:

In [ ]:
first_token_id = tokenized_example["input_ids"][0][1]
offsets = tokenized_example["offset_mapping"][0][1]
print(tokenizer.convert_ids_to_tokens([first_token_id])[0], example["question"][offsets[0]:offsets[1]])

ক [{'input_text': 'কবে থেকে নিয়মিতই পেঁয়াজ আসবে?', 'turn_id': 1}]


So we can use this mapping to find the position of the start and end tokens of our answer in a given feature. We just have to distinguish which parts of the offsets correspond to the question and which part correspond to the context, this is where the `sequence_ids` method of our `tokenized_example` can be useful:

In [ ]:
sequence_ids = tokenized_example.sequence_ids()
print(sequence_ids)

[None, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, None, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, None]


It returns `None` for the special tokens, then 0 or 1 depending on whether the corresponding token comes from the first sentence past (the question) or the second (the context). Now with all of this, we can find the first and last token of the answer in one of our input feature (or if the answer is not in this feature):

In [ ]:
answers = example["answers"][0]['input_text']
print(answers)
answers = example["answers"][0]
start_char = answers["input_text"][0]
print(start_char)
end_char = start_char + str(len(answers["span_text"]))
print(end_char)

ডিসেম্বর 
ড
ড33


In [ ]:
answers = example["answers"][0]
start_char = answers['span_start']
end_char = answers['span_end']

# Start token index of the current span in the text.
token_start_index = 0
while sequence_ids[token_start_index] != 1:
    token_start_index += 1

# End token index of the current span in the text.
token_end_index = len(tokenized_example["input_ids"][0]) - 1
while sequence_ids[token_end_index] != 1:
    token_end_index -= 1

# Detect if the answer is out of the span (in which case this feature is labeled with the CLS index).
offsets = tokenized_example["offset_mapping"][0]
if (offsets[token_start_index][0] <= start_char and offsets[token_end_index][1] >= end_char):
    # Move the token_start_index and token_end_index to the two ends of the answer.
    # Note: we could go after the last offset if the answer is the last word (edge case).
    while token_start_index < len(offsets) and offsets[token_start_index][0] <= start_char:
        token_start_index += 1
    start_position = token_start_index - 1
    while offsets[token_end_index][1] >= end_char:
        token_end_index -= 1
    end_position = token_end_index + 1
    print(start_position, end_position)
else:
    print("The answer is not in this feature.")

39 64


And we can double check that it is indeed the theoretical answer:

In [ ]:
print(tokenizer.decode(tokenized_example["input_ids"][0][start_position: end_position+1]))
print(answers["span_text"])

ডিসেমবর থেকে নিযমিতই পেযাজ আসব
ডিসেম্বর থেকে নিয়মিতই পেঁয়াজ আসবে


For this notebook to work with any kind of models, we need to account for the special case where the model expects padding on the left (in which case we switch the order of the question and the context):

In [ ]:
pad_on_right = tokenizer.padding_side == "right"

Now let's put everything together in one function we will apply to our training set. In the case of impossible answers (the answer is in another feature given by an example with a long context), we set the cls index for both the start and end position. We could also simply discard those examples from the training set if the flag `allow_impossible_answers` is `False`. Since the preprocessing is already complex enough as it is, we've kept is simple for this part.

In [ ]:
def prepare_train_features(examples):
    # Tokenize the question and context
    inputs= tokenizer(examples['question'][0]['input_text'], examples['story'], return_tensors="pt")

    # Get model outputs for start and end positions of the answer
    with torch.no_grad():
        outputs = model(**inputs)
    start_scores = outputs.start_logits
    end_scores = outputs.end_logits

    # Find the best start and end position indices
    start_index = torch.argmax(start_scores)
    end_index = torch.argmax(end_scores) + 1
    # Get the answer using the indices and decode it
    answer = tokenizer.decode(inputs["input_ids"][0, start_index:end_index])

    return answer

This function works with one or several examples. In the case of several examples, the tokenizer will return a list of lists for each key:

In [ ]:
for i, example in enumerate(datasets["train"]):

    features = prepare_train_features(example)
    if i==1:
        break



## Fine-tuning the model

Now that our data is ready for training, we can download the pretrained model and fine-tune it. Since our task is question answering, we use the `AutoModelForQuestionAnswering` class. Like with the tokenizer, the `from_pretrained` method will download and cache the model for us:

This ***Approach 1*** uses context value to extract information and answer user Questions using the specific model ***shams/banglabert-finetuned-squad***

In [ ]:
def answer_question(question, context):
    # Tokenize the question and context
    inputs = tokenizer(question, context, return_tensors="pt")

    # Get model outputs for start and end positions of the answer
    with torch.no_grad():
        outputs = model(**inputs)
    start_scores = outputs.start_logits
    end_scores = outputs.end_logits

    # Find the best start and end position indices
    start_index = torch.argmax(start_scores)
    end_index = torch.argmax(end_scores) + 1
    # Get the answer using the indices and decode it
    answer = tokenizer.decode(inputs["input_ids"][0, start_index:end_index])

    return answer

In [ ]:
for i, example in enumerate(datasets["train"]):
        print(example['story'])
        if i == 1:
            break

টিকফা চুক্তিতে স্বাক্ষর করলে বাংলাদেশের জাতীয় নিরাপত্তা যুক্তরাষ্ট্রের হাতে চলে যাবে। গতকাল সোমবার বাংলাদেশের ওয়ার্কার্স পার্টির পলিটব্যুরোর সভায় গৃহীত প্রস্তাবে এ কথা বলা হয়।এ চুক্তির প্রতিবাদে ১৯ মে রোববার দেশব্যাপী বিক্ষোভ দিবস পালন করার আহ্বান জানানো হয়।দলের সভাপতি রাশেদ খান মেননের সভাপতিত্বে অনুষ্ঠিত সভায় উপস্থিত ছিলেন সাধারণ সম্পাদক আনিসুর রহমান মল্লিক সাংসদ ফজলে হোসেন বাদশা হাজেরা সুলতানা প্রমুখ।অপর এক প্রস্তাবে পোশাকশিল্পে মজুরি বোর্ড গঠন করায় সন্তোষ প্রকাশ করা হয়। বিজ্ঞপ্তি।

সাম্প্রদায়িক উসকানি ও মানহানির অভিযোগে করা বিএনপির স্থায়ী কমিটির সদস্য এম কে আনোয়ারের দুই সপ্তাহের জামিন মঞ্জুর করেছেন হাইকোর্ট। গতকাল সোমবার বিচারপতি সালমা মাসুদ চৌধুরী ও বিচারপতি মো জাহাঙ্গীর হোসেনের সমন্বয়ে গঠিত হাইকোর্টের একটি বেঞ্চ এই জামিন মঞ্জুর করেন।গতকাল আদালতে হাজির হয়ে এম কে আনোয়ার আইনজীবীর মাধ্যমে জামিনের আবেদন করেন। ৭ মে স্বেচ্ছাসেবক লীগের নেতা দেবাশীষ বাদী হয়ে ঢাকার মুখ্য মহানগর হাকিম আদালতে সাম্প্রদায়িক উসকানি ও মানহানির অভিযোগে এম কে আনোয়ারের বিরুদ্ধে মামলা করেন। মহানগর হা

In [ ]:
while True:
    user_input = input("User: ")
    if user_input.lower() in ["exit", "quit"]:
        break  # Exit loop if user enters 'exit' or 'quit'
    for i, example in enumerate(datasets["train"]):

        bot_response = answer_question(user_input,example['story'])
        if i==1:
            break
    print("Chatbot:", bot_response)

User: দলের সভাপতি কে?
Chatbot: [CLS]
User: exi
Chatbot: [CLS]
User: exit


On the other hand ***Approch 2***, uses same model but different Handling Technique of ***Data***.

In [ ]:
with open("intents.json", "r", encoding="utf-8") as file:
    intents = json.load(file)["intents"]

def answer_question(user_input, intents):
    # Check if user input matches any intent patterns
    for data in intents:
        for pattern in data["patterns"]:
            if pattern in user_input:
                return random.choice(data["responses"]), 1.0  # High confidence for intents

    # If no intent is matched, use the question-answering model
    try:
        inputs = tokenizer(user_input, return_tensors="pt")
    except Exception as e:
        print(f"Error during tokenization: {e}")
        return "I'm sorry, I couldn't understand that.", 0.0  # Low confidence for errors

    with torch.no_grad():
        outputs = model(**inputs)
    start_scores = outputs.start_logits
    end_scores = outputs.end_logits

    # Calculate confidence and adjust the threshold as needed
    confidence = torch.max(torch.softmax(start_scores, dim=1)) * torch.max(torch.softmax(end_scores, dim=1))

    if confidence.item() > 0.5:
        start_index = torch.argmax(start_scores)
        end_index = torch.argmax(end_scores) + 1
        answer = tokenizer.decode(inputs["input_ids"][0, start_index:end_index])
        return answer, confidence.item()
    else:
        return "I'm not sure about that.", confidence.item()

# Welcome message
print("Chatbot: Hi there! I'm here to help. Type 'exit' or 'quit' to end the conversation.")

while True:
    user_input = input("User: ")

    # Improved exit condition
    if any(keyword in user_input.lower() for keyword in ["exit", "quit", "goodbye", "see you later"]):
        print("Chatbot: Goodbye! Have a great day.")
        break

    bot_response, confidence = answer_question(user_input, intents)
    print(f"Chatbot (confidence: ): {bot_response}")

Chatbot: Hi there! I'm here to help. Type 'exit' or 'quit' to end the conversation.
User: আপনি কেমন আছেন?
Chatbot (confidence: ): হ্যালো
User: exit
Chatbot: Goodbye! Have a great day.


In Here we have combined both ***Approch 1*** and ***Approch 2*** where two functions were made, one works with context and the others works with our **DATA**.

In [ ]:
def answer_question_with_context(user_input, context):
    # Use the question-answering model with context
    inputs = tokenizer(user_input, context, return_tensors="pt")

    with torch.no_grad():
        outputs = model(**inputs)
    start_scores = outputs.start_logits
    end_scores = outputs.end_logits

    start_index = torch.argmax(start_scores)
    end_index = torch.argmax(end_scores) + 1
    answer = tokenizer.decode(inputs["input_ids"][0, start_index:end_index])

    return answer

def answer_question_based_on_intent(user_input, intents):
    # Check if user input matches any intent patterns
    for data in intents:
        for pattern in data["patterns"]:
            if pattern in user_input:
                return data["responses"][0]

    return None

# Load intents from a separate file
with open("intents.json", "r", encoding="utf-8") as file:
    intents = json.load(file)["intents"]

while True:
    user_input = input("User: ")
    if user_input.lower() in ["exit", "quit"]:
        break

    # Check if there's a specific response based on intent
    intent_response = answer_question_based_on_intent(user_input, intents)
    if intent_response:
        print("Chatbot:", intent_response)
    else:
        for i, example in enumerate(datasets["train"]):

            context_response = answer_question_with_context(user_input,example['story'])
            if i==1:
                break
        print("Chatbot:", context_response)

User: আপনি কে?
Chatbot: আমি টেড, একটি ডিপ-লার্নিং চ্যাটবট
User: টিকফা চুক্তিতে স্বাক্ষর করলে বাংলাদেশের জাতীয় নিরাপত্তা কাদের হাতে চলে যাবে?
Chatbot: যুক্তরাষ্ট্রের
User: exit
